In [1]:
import pandas as pd
import numpy as np
from collections import defaultdict
import re

In [2]:
step_1 = pd.read_csv('data/news_mpb_bond.csv')

In [3]:
step_1.rename(columns={'values' : 'sentiment'}, inplace= True)

In [4]:
training_set = np.array(pd.DataFrame({"doc" : step_1['token_ngram'], "point" : step_1['sentiment']}).fillna(""))

In [5]:
wordfreq = defaultdict(lambda : [0,0])

for doc, point in training_set[:252248]:
    try :
        for word in doc.replace('[', "").replace(']', "").replace('"', "").replace(' ', "").replace("'","").split('.'):

            if point == 1.0 :
                wordfreq[word][0] += 1

            elif point == -1.0 :
                wordfreq[word][1] += 1

    except Exception as ex:
        print("에러2 ", ex)
        
for doc, point in training_set[252248:]:
    try :
        for word in doc.replace('[', "").replace(']', "").replace('"', "").replace(' ', "").replace("'","").split(','):

            if point == 1.0 :
                wordfreq[word][0] += 1

            elif point == -1.0 :
                wordfreq[word][1] += 1

    except Exception as ex:
        print("에러2 ", ex)

In [6]:
wordfreq_df = pd.DataFrame.from_dict(wordfreq, orient='index', columns=['Hawkish', 'Dovish'])

In [7]:
wordfreq_df.to_csv('data/news_bond_mpb_wordfreq.csv')

In [8]:
wordfreq_df

Hawkish   Dovish
fed/NNG;금리/NNG;인하/NNG                     1712     1705
fed/NNG;금리/NNG;인상/NNG                     3706     4532
주택시장/NNG;과열/NNG                             33       58
지수/NNG;하락/NNG                             1236     1464
경기/NNG;침체/NNG                             1085     1859
경기/NNG;둔화/NNG                             2121     1939
실적/NNG;증가/NNG                              114      123
장단기/NNG                                   1584     1404
금리/NNG                                  378862   422541
역전/NNG                                    2575     2576
현상/NNG                                   10263    12258
국제/NNG                                   24575    25464
유가/NNG                                   29531    27907
흐름/NNG                                   17718    18994
관심/NNG                                   13147    14499
기울이/VV                                     459      507
조심/NNG                                    2184     2437
태도/NNG                                    2487     2689
임할/VV                                       18       48
예상/NNG                                   88171    92889
되/VV                                    371192   407501
블루칩/NNG                                    772      724
위주/NNG                                    4117     4482
다우존스산업평균지수/NNG                            8747    10286
포인트/NNG                                  58176    71496
하락/NNG                                  134079   147335
하/XSV                                   435981   486827
비해/VV                                    12566    12598
하/VV                                    951640  1065069
거래/NNG                                   55467    60786
...                                        ...      ...
활경/NNG                                       1        0
자법/NNG                                       1        0
민세/NNG                                       1        0
거영/NNG                                       1        0
금리/NNG;전망/NNG;약세/NNG                         1        0
아이엔에스/NNG                                    0        1
채농/NNG                                       0        1
지표/NNG;열위/NNG                                0        1
신용스프레드/NNG;회사채/NNG;축소/NNG                    0        1
하향/NNG;경제/NNG;회복/NNG                         0        1
높/VA;등급/NNG;하락/NNG                           0        2
산업활동/NNG;상승/NNG                              0        1
어회/NNG                                       1        0
복국/NNG                                       1        0
상회/NNG;호조/NNG                                1        0
어렴/NNG                                       0        1
국고채/NNG;금리/NNG;하락/NNG;스프레드/NNG;확대/NNG        0        1
크레딧/NNG;국고채/NNG;금리/NNG;하락/NNG                0        1
크레딧/NNG;가격/NNG;부담/NNG                        0        1
하향/NNG;불확실성/NNG                              0        1
단기물/NNG;일시적/VAX                              0        1
생산자제품재고지수/NNG                                0        1
금리/NNG;추이/NNG;금리/NNG;상승/NNG                  1        0
커버넌트/NNG                                     0        2
사채발행요건/NNG                                   0        1
국고채/NNG;발행/NNG;유보/NNG                        1        0
총교/NNG                                       0        1
인상/NNG;국채/NNG;금리/NNG;상승/NNG                  1        0
감극/NNG                                       1        0
선진국/NNG;금리/NNG;하향/NNG                        1        0

[137760 rows x 2 columns]

In [9]:
doccnt1 = 0
doccnt0 = 0

for key, (cnt1, cnt0) in wordfreq.items():
    if cnt1 > 0 :
        doccnt1 += cnt1
        
    if cnt0 > 0 :
        doccnt0 += cnt0

In [10]:
k = 0.5

wordprobs = defaultdict(lambda : [0, 0])

for key, (cnt1, cnt0) in wordfreq.items() :
    
    wordprobs[key][0] = (cnt1 + k) / (doccnt1 + 2*k)
    wordprobs[key][1] = (cnt0 + k) / (doccnt0 + 2*k)

In [11]:
a = pd.DataFrame.from_dict(wordprobs, orient = 'index', columns=['Haw_prob', 'Dov_prob'])

wordfreq_df['Haw_prob'] = a['Haw_prob']

wordfreq_df['Dov_prob'] = a['Dov_prob']

In [12]:
a = pd.DataFrame.from_dict(wordprobs, orient = 'index', columns=['Haw_prob', 'Dov_prob'])

wordfreq_df['Haw_prob'] = a['Haw_prob']

wordfreq_df['Dov_prob'] = a['Dov_prob']

In [13]:
wordfreq_df.to_csv('data/news_mpb_bond_wordfreq.csv')

In [14]:
a = pd.read_csv('data/news_mpb_bond_wordfreq.csv')

In [15]:
a

Unnamed: 0  Hawkish   Dovish      Haw_prob  \
0                       fed/NNG;금리/NNG;인하/NNG     1712     1705  8.855054e-05   
1                       fed/NNG;금리/NNG;인상/NNG     3706     4532  1.916570e-04   
2                             주택시장/NNG;과열/NNG       33       58  1.732230e-06   
3                               지수/NNG;하락/NNG     1236     1464  6.393737e-05   
4                               경기/NNG;침체/NNG     1085     1859  5.612941e-05   
5                               경기/NNG;둔화/NNG     2121     1939  1.096993e-04   
6                               실적/NNG;증가/NNG      114      123  5.920606e-06   
7                                     장단기/NNG     1584     1404  8.193187e-05   
8                                      금리/NNG   378862   422541  1.959035e-02   
9                                      역전/NNG     2575     2576  1.331748e-04   
10                                     현상/NNG    10263    12258  5.307086e-04   
11                                     국제/NNG    24575    25464  1.270758e-03   
12                                     유가/NNG    29531    27907  1.527025e-03   
13                                     흐름/NNG    17718    18994  9.161943e-04   
14                                     관심/NNG    13147    14499  6.798355e-04   
15                                     기울이/VV      459      507  2.375998e-05   
16                                     조심/NNG     2184     2437  1.129569e-04   
17                                     태도/NNG     2487     2689  1.286245e-04   
18                                      임할/VV       18       48  9.566044e-07   
19                                     예상/NNG    88171    92889  4.559202e-03   
20                                       되/VV   371192   407501  1.919375e-02   
21                                    블루칩/NNG      772      724  3.994470e-05   
22                                     위주/NNG     4117     4482  2.129091e-04   
23                             다우존스산업평균지수/NNG     8747    10286  4.523188e-04   
24                                    포인트/NNG    58176    71496  3.008211e-03   
25                                     하락/NNG   134079   147335  6.933029e-03   
26                                      하/XSV   435981   486827  2.254388e-02   
27                                      비해/VV    12566    12598  6.497929e-04   
28                                       하/VV   951640  1065069  4.920776e-02   
29                                     거래/NNG    55467    60786  2.868133e-03   
...                                       ...      ...      ...           ...   
137730                                 활경/NNG        1        0  7.756252e-08   
137731                                 자법/NNG        1        0  7.756252e-08   
137732                                 민세/NNG        1        0  7.756252e-08   
137733                                 거영/NNG        1        0  7.756252e-08   
137734                   금리/NNG;전망/NNG;약세/NNG        1        0  7.756252e-08   
137735                              아이엔에스/NNG        0        1  2.585417e-08   
137736                                 채농/NNG        0        1  2.585417e-08   
137737                          지표/NNG;열위/NNG        0        1  2.585417e-08   
137738              신용스프레드/NNG;회사채/NNG;축소/NNG        0        1  2.585417e-08   
137739                   하향/NNG;경제/NNG;회복/NNG        0        1  2.585417e-08   
137740                     높/VA;등급/NNG;하락/NNG        0        2  2.585417e-08   
137741                        산업활동/NNG;상승/NNG        0        1  2.585417e-08   
137742                                 어회/NNG        1        0  7.756252e-08   
137743                                 복국/NNG        1        0  7.756252e-08   
137744                          상회/NNG;호조/NNG        1        0  7.756252e-08   
137745                                 어렴/NNG        0        1  2.585417e-08   
137746  국고채/NNG;금리/NNG;하락/NNG;스프레드/NNG;확대/NNG        0        1  2.585417e-08   
137747          크레딧/NNG;국고채/NNG;금리/NNG;하락/NNG        0        1  2

In [16]:
a['Haw_con_pro'] = pd.Series(a['Haw_prob'] / (a['Haw_prob'] + a['Dov_prob']))
a['Dov_con_pro'] = pd.Series(a['Dov_prob'] / (a['Haw_prob'] + a['Dov_prob']))
a['polarity'] = pd.Series(a['Haw_con_pro'] / a['Dov_con_pro'])

In [17]:
a.rename(columns={"Unnamed: 0" : "word"}, inplace = True)

In [18]:
a.to_csv('data/news_bond_mpb_con_pro.csv', index = False)

In [19]:
intensity_list = []
for i in range(len(a['Haw_con_pro'])):
    
    if ( a['Haw_con_pro'][i] >= a['Dov_con_pro'][i] ):
        intensity = ( a['Haw_con_pro'][i] / a['Dov_con_pro'][i] )
        intensity_list.append(intensity)
        
    else:
        intensity = ( a['Dov_con_pro'][i] / a['Haw_con_pro'][i]) 
        intensity_list.append(intensity)

In [20]:
a['intensity'] = pd.Series(intensity_list).values

In [21]:
a

word  Hawkish   Dovish      Haw_prob  \
0                       fed/NNG;금리/NNG;인하/NNG     1712     1705  8.855054e-05   
1                       fed/NNG;금리/NNG;인상/NNG     3706     4532  1.916570e-04   
2                             주택시장/NNG;과열/NNG       33       58  1.732230e-06   
3                               지수/NNG;하락/NNG     1236     1464  6.393737e-05   
4                               경기/NNG;침체/NNG     1085     1859  5.612941e-05   
5                               경기/NNG;둔화/NNG     2121     1939  1.096993e-04   
6                               실적/NNG;증가/NNG      114      123  5.920606e-06   
7                                     장단기/NNG     1584     1404  8.193187e-05   
8                                      금리/NNG   378862   422541  1.959035e-02   
9                                      역전/NNG     2575     2576  1.331748e-04   
10                                     현상/NNG    10263    12258  5.307086e-04   
11                                     국제/NNG    24575    25464  1.270758e-03   
12                                     유가/NNG    29531    27907  1.527025e-03   
13                                     흐름/NNG    17718    18994  9.161943e-04   
14                                     관심/NNG    13147    14499  6.798355e-04   
15                                     기울이/VV      459      507  2.375998e-05   
16                                     조심/NNG     2184     2437  1.129569e-04   
17                                     태도/NNG     2487     2689  1.286245e-04   
18                                      임할/VV       18       48  9.566044e-07   
19                                     예상/NNG    88171    92889  4.559202e-03   
20                                       되/VV   371192   407501  1.919375e-02   
21                                    블루칩/NNG      772      724  3.994470e-05   
22                                     위주/NNG     4117     4482  2.129091e-04   
23                             다우존스산업평균지수/NNG     8747    10286  4.523188e-04   
24                                    포인트/NNG    58176    71496  3.008211e-03   
25                                     하락/NNG   134079   147335  6.933029e-03   
26                                      하/XSV   435981   486827  2.254388e-02   
27                                      비해/VV    12566    12598  6.497929e-04   
28                                       하/VV   951640  1065069  4.920776e-02   
29                                     거래/NNG    55467    60786  2.868133e-03   
...                                       ...      ...      ...           ...   
137730                                 활경/NNG        1        0  7.756252e-08   
137731                                 자법/NNG        1        0  7.756252e-08   
137732                                 민세/NNG        1        0  7.756252e-08   
137733                                 거영/NNG        1        0  7.756252e-08   
137734                   금리/NNG;전망/NNG;약세/NNG        1        0  7.756252e-08   
137735                              아이엔에스/NNG        0        1  2.585417e-08   
137736                                 채농/NNG        0        1  2.585417e-08   
137737                          지표/NNG;열위/NNG        0        1  2.585417e-08   
137738              신용스프레드/NNG;회사채/NNG;축소/NNG        0        1  2.585417e-08   
137739                   하향/NNG;경제/NNG;회복/NNG        0        1  2.585417e-08   
137740                     높/VA;등급/NNG;하락/NNG        0        2  2.585417e-08   
137741                        산업활동/NNG;상승/NNG        0        1  2.585417e-08   
137742                                 어회/NNG        1        0  7.756252e-08   
137743                                 복국/NNG        1        0  7.756252e-08   
137744                          상회/NNG;호조/NNG        1        0  7.756252e-08   
137745                                 어렴/NNG        0        1  2.585417e-08   
137746  국고채/NNG;금리/NNG;하락/NNG;스프레드/NNG;확대/NNG        0        1  2.585417e-08   
137747          크레딧/NNG;국고채/NNG;금리/NNG;하락/NNG        0        1  2.58541

In [22]:
a.to_csv('data/news_bond_mpb_intensity.csv', index = False)

In [31]:
z = pd.read_csv('data/news_bond_mpb_intensity.csv')

In [32]:
z[z.word == '절상/NNG']

word  Hawkish  Dovish  Haw_prob  Dov_prob  Haw_con_pro  Dov_con_pro  \
361  절상/NNG     6124    4849  0.000317  0.000224     0.586126     0.413874   

     polarity  intensity  
361  1.416194   1.416194

In [23]:
a = pd.read_csv('data/news_bond_mpb_intensity.csv')

In [24]:
intensity_index = a.index[a['intensity'] <= 1.3].tolist()

In [25]:
a.drop(a.index[intensity_index], inplace = True)

In [26]:
a.to_csv('data/news_bond_mpb_intensity.csv', index = False)

In [31]:
b = pd.read_csv('data/news_bond_mpb_intensity.csv')

In [32]:
index_list3 = []
for i in range(len(b['word'])):
    print(i)
    try:
        a = re.findall('(.+)/', b['word'][i])[0]
    except Exception as ex:
        print('에러', ex)
    
    
    if len(a) == 1:
        index_list3.append(i)

b.drop(b.index[index_list3], inplace = True)

b.to_csv('data/news_bond_mpb_intensity.csv', index = False)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

4587
4588
4589
4590
4591
4592
4593
4594
4595
4596
4597
4598
4599
4600
4601
4602
4603
4604
4605
4606
4607
4608
4609
4610
4611
4612
4613
4614
4615
4616
4617
4618
4619
4620
4621
4622
4623
4624
4625
4626
4627
4628
4629
4630
4631
4632
4633
4634
4635
4636
4637
4638
4639
4640
4641
4642
4643
4644
4645
4646
4647
4648
4649
4650
4651
4652
4653
4654
4655
4656
4657
4658
4659
4660
4661
4662
4663
4664
4665
4666
4667
4668
4669
4670
4671
4672
4673
4674
4675
4676
4677
4678
4679
4680
4681
4682
4683
4684
4685
4686
4687
4688
4689
4690
4691
4692
4693
4694
4695
4696
4697
4698
4699
4700
4701
4702
4703
4704
4705
4706
4707
4708
4709
4710
4711
4712
4713
4714
4715
4716
4717
4718
4719
4720
4721
4722
4723
4724
4725
4726
4727
4728
4729
4730
4731
4732
4733
4734
4735
4736
4737
4738
4739
4740
4741
4742
4743
4744
4745
4746
4747
4748
4749
4750
4751
4752
4753
4754
4755
4756
4757
4758
4759
4760
4761
4762
4763
4764
4765
4766
4767
4768
4769
4770
4771
4772
4773
4774
4775
4776
4777
4778
4779
4780
4781
4782
4783
4784
4785
4786


6732
6733
6734
6735
6736
6737
6738
6739
6740
6741
6742
6743
6744
6745
6746
6747
6748
6749
6750
6751
6752
6753
6754
6755
6756
6757
6758
6759
6760
6761
6762
6763
6764
6765
6766
6767
6768
6769
6770
6771
6772
6773
6774
6775
6776
6777
6778
6779
6780
6781
6782
6783
6784
6785
6786
6787
6788
6789
6790
6791
6792
6793
6794
6795
6796
6797
6798
6799
6800
6801
6802
6803
6804
6805
6806
6807
6808
6809
6810
6811
6812
6813
6814
6815
6816
6817
6818
6819
6820
6821
6822
6823
6824
6825
6826
6827
6828
6829
6830
6831
6832
6833
6834
6835
6836
6837
6838
6839
6840
6841
6842
6843
6844
6845
6846
6847
6848
6849
6850
6851
6852
6853
6854
6855
6856
6857
6858
6859
6860
6861
6862
6863
6864
6865
6866
6867
6868
6869
6870
6871
6872
6873
6874
6875
6876
6877
6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931


9675
9676
9677
9678
9679
9680
9681
9682
9683
9684
9685
9686
9687
9688
9689
9690
9691
9692
9693
9694
9695
9696
9697
9698
9699
9700
9701
9702
9703
9704
9705
9706
9707
9708
9709
9710
9711
9712
9713
9714
9715
9716
9717
9718
9719
9720
9721
9722
9723
9724
9725
9726
9727
9728
9729
9730
9731
9732
9733
9734
9735
9736
9737
9738
9739
9740
9741
9742
9743
9744
9745
9746
9747
9748
9749
9750
9751
9752
9753
9754
9755
9756
9757
9758
9759
9760
9761
9762
9763
9764
9765
9766
9767
9768
9769
9770
9771
9772
9773
9774
9775
9776
9777
9778
9779
9780
9781
9782
9783
9784
9785
9786
9787
9788
9789
9790
9791
9792
9793
9794
9795
9796
9797
9798
9799
9800
9801
9802
9803
9804
9805
9806
9807
9808
9809
9810
9811
9812
9813
9814
9815
9816
9817
9818
9819
9820
9821
9822
9823
9824
9825
9826
9827
9828
9829
9830
9831
9832
9833
9834
9835
9836
9837
9838
9839
9840
9841
9842
9843
9844
9845
9846
9847
9848
9849
9850
9851
9852
9853
9854
9855
9856
9857
9858
9859
9860
9861
9862
9863
9864
9865
9866
9867
9868
9869
9870
9871
9872
9873
9874


12631
12632
12633
12634
12635
12636
12637
12638
12639
12640
12641
12642
12643
12644
12645
12646
12647
12648
12649
12650
12651
12652
12653
12654
12655
12656
12657
12658
12659
12660
12661
12662
12663
12664
12665
12666
12667
12668
12669
12670
12671
12672
12673
12674
12675
12676
12677
12678
12679
12680
12681
12682
12683
12684
12685
12686
12687
12688
12689
12690
12691
12692
12693
12694
12695
12696
12697
12698
12699
12700
12701
12702
12703
12704
12705
12706
12707
12708
12709
12710
12711
12712
12713
12714
12715
12716
12717
12718
12719
12720
12721
12722
12723
12724
12725
12726
12727
12728
12729
12730
12731
12732
12733
12734
12735
12736
12737
12738
12739
12740
12741
12742
12743
12744
12745
12746
12747
12748
12749
12750
12751
12752
12753
12754
12755
12756
12757
12758
12759
12760
12761
12762
12763
12764
12765
12766
12767
12768
12769
12770
12771
12772
12773
12774
12775
12776
12777
12778
12779
12780
12781
12782
12783
12784
12785
12786
12787
12788
12789
12790
12791
12792
12793
12794
12795
12796
1279

...

87851
87852
87853
87854
87855
87856
87857
87858
87859
87860
87861
87862
87863
87864
87865
87866
87867
87868
87869
87870
87871
87872
87873
87874
87875
87876
87877
87878
87879
87880
87881
87882
87883
87884
87885
87886
87887
87888
87889
87890
87891
87892
87893
87894
87895
87896
87897
87898
87899
87900
87901
87902
87903
87904
87905
87906
87907
87908
87909
87910
87911
87912
87913
87914
87915
87916
87917
87918
87919
87920
87921
87922
87923
87924
87925
87926
87927
87928
87929
87930
87931
87932
87933
87934
87935
87936
87937
87938
87939
87940
87941
87942
87943
87944
87945
87946
87947
87948
87949
87950
87951
87952
87953
87954
87955
87956
87957
87958
87959
87960
87961
87962
87963
87964
87965
87966
87967
87968
87969
87970
87971
87972
87973
87974
87975
87976
87977
87978
87979
87980
87981
87982
87983
87984
87985
87986
87987
87988
87989
87990
87991
87992
87993
87994
87995
87996
87997
87998
87999
88000
88001
88002
88003
88004
88005
88006
88007
88008
88009
88010
88011
88012
88013
88014
88015
88016
8801

90708
90709
90710
90711
90712
90713
90714
90715
90716
90717
90718
90719
90720
90721
90722
90723
90724
90725
90726
90727
90728
90729
90730
90731
90732
90733
90734
90735
90736
90737
90738
90739
90740
90741
90742
90743
90744
90745
90746
90747
90748
90749
90750
90751
90752
90753
90754
90755
90756
90757
90758
90759
90760
90761
90762
90763
90764
90765
90766
90767
90768
90769
90770
90771
90772
90773
90774
90775
90776
90777
90778
90779
90780
90781
90782
90783
90784
90785
90786
90787
90788
90789
90790
90791
90792
90793
90794
90795
90796
90797
90798
90799
90800
90801
90802
90803
90804
90805
90806
90807
90808
90809
90810
90811
90812
90813
90814
90815
90816
90817
90818
90819
90820
90821
90822
90823
90824
90825
90826
90827
90828
90829
90830
90831
90832
90833
90834
90835
90836
90837
90838
90839
90840
90841
90842
90843
90844
90845
90846
90847
90848
90849
90850
90851
90852
90853
90854
90855
90856
90857
90858
90859
90860
90861
90862
90863
90864
90865
90866
90867
90868
90869
90870
90871
90872
90873
9087

93110
93111
93112
93113
93114
93115
93116
93117
93118
93119
93120
93121
93122
93123
93124
93125
93126
93127
93128
93129
93130
93131
93132
93133
93134
93135
93136
93137
93138
93139
93140
93141
93142
93143
93144
93145
93146
93147
93148
93149
93150
93151
93152
93153
93154
93155
93156
93157
93158
93159
93160
93161
93162
93163
93164
93165
93166
93167
93168
93169
93170
93171
93172
93173
93174
93175
93176
93177
93178
93179
93180
93181
93182
93183
93184
93185
93186
93187
93188
93189
93190
93191
93192
93193
93194
93195
93196
93197
93198
93199
93200
93201
93202
93203
93204
93205
93206
93207
93208
93209
93210
93211
93212
93213
93214
93215
93216
93217
93218
93219
93220
93221
93222
93223
93224
93225
93226
93227
93228
93229
93230
93231
93232
93233
93234
93235
93236
93237
93238
93239
93240
93241
93242
93243
93244
93245
93246
93247
93248
93249
93250
93251
93252
93253
93254
93255
93256
93257
93258
93259
93260
93261
93262
93263
93264
93265
93266
93267
93268
93269
93270
93271
93272
93273
93274
93275
9327

95707
95708
95709
95710
95711
95712
95713
95714
95715
95716
95717
95718
95719
95720
95721
95722
95723
95724
95725
95726
95727
95728
95729
95730
95731
95732
95733
95734
95735
95736
95737
95738
95739
95740
95741
95742
95743
95744
95745
95746
95747
95748
95749
95750
95751
95752
95753
95754
95755
95756
95757
95758
95759
95760
95761
95762
95763
95764
95765
95766
95767
95768
95769
95770
95771
95772
95773
95774
95775
95776
95777
95778
95779
95780
95781
95782
95783
95784
95785
95786
95787
95788
95789
95790
95791
95792
95793
95794
95795
95796
95797
95798
95799
95800
95801
95802
95803
95804
95805
95806
95807
95808
95809
95810
95811
95812
95813
95814
95815
95816
95817
95818
95819
95820
95821
95822
95823
95824
95825
95826
95827
95828
95829
95830
95831
95832
95833
95834
95835
95836
95837
95838
95839
95840
95841
95842
95843
95844
95845
95846
95847
95848
95849
95850
95851
95852
95853
95854
95855
95856
95857
95858
95859
95860
95861
95862
95863
95864
95865
95866
95867
95868
95869
95870
95871
95872
9587

98205
98206
98207
98208
98209
98210
98211
98212
98213
98214
98215
98216
98217
98218
98219
98220
98221
98222
98223
98224
98225
98226
98227
98228
98229
98230
98231
98232
98233
98234
98235
98236
98237
98238
98239
98240
98241
98242
98243
98244
98245
98246
98247
98248
98249
98250
98251
98252
98253
98254
98255
98256
98257
98258
98259
98260
98261
98262
98263
98264
98265
98266
98267
98268
98269
98270
98271
98272
98273
98274
98275
98276
98277
98278
98279
98280
98281
98282
98283
98284
98285
98286
98287
98288
98289
98290
98291
98292
98293
98294
98295
98296
98297
98298
98299
98300
98301
98302
98303
98304
98305
98306
98307
98308
98309
98310
98311
98312
98313
98314
98315
98316
98317
98318
98319
98320
98321
98322
98323
98324
98325
98326
98327
98328
98329
98330
98331
98332
98333
98334
98335
98336
98337
98338
98339
98340
98341
98342
98343
98344
98345
98346
98347
98348
98349
98350
98351
98352
98353
98354
98355
98356
98357
98358
98359
98360
98361
98362
98363
98364
98365
98366
98367
98368
98369
98370
9837

In [33]:
len(b)

97012

In [124]:
index_list = []
for i in range(len(b)):
    try:
        if (b['Hawkish'].loc[i] + b['Dovish'].loc[i]) <= 15:
            print(b['word'].loc[i], " , ", b['Hawkish'].loc[i] + b['Dovish'].loc[i])
            index_list.append(i)
            
    except:
        print("에러")

일어났으며/VV  ,  10
납회/NNG  ,  11
발회/NNG  ,  1
추정실적/NNG  ,  14
하반부/NNG  ,  1
무역/NNG;재정/NNG;적자/NNG  ,  13
가로놓여/VV  ,  3
자기반성/NNG  ,  7
신관/NNG  ,  14
戌年/NNG  ,  2
바꿔치기/NNG  ,  13
오곡밥/NNG  ,  2
떡국/NNG  ,  3
경기/NNG;회복/NNG;콜/NNG;금리/NNG;인상/NNG  ,  8
채권/NNG;금리/NNG;경기/NNG;회복/NNG  ,  6
금리/NNG;인상/NNG;압력/NNG;줄/VV  ,  14
내수/NNG;성장기여도/NNG;높/VA  ,  9
수출/NNG;견실/NNG;성장/NNG  ,  4
대표채권/NNG  ,  12
중소기업/NNG;위험/NNG  ,  13
자본/NNG;강화/NNG  ,  11
동력화/NNG  ,  5
혁신학교/NNG  ,  10
될려면/VV  ,  1
장류/NNG  ,  13
기대/NNG;국채/NNG;수익률/NNG;상승/NNG  ,  8
금융시장/NNG;경제/NNG;회복/NNG  ,  5
가격/NNG;하향/NNG;압력/NNG  ,  15
강하/VA;경제/NNG;회복/NNG  ,  13
디플레이션/NNG;해소/NNG  ,  10
gdp/NNG;성장률/NNG;웃돌/VV  ,  10
흐릴/VV  ,  5
금리/NNG;정책/NNG;완화/NNG  ,  10
수출/NNG;설비/NNG;투자/NNG;증가/NNG  ,  9
생산/NNG;시장/NNG;예상/NNG;넘/VV  ,  7
경기/NNG;침체/NNG;둔화/NNG  ,  11
소비/NNG;지표/NNG;견조/NNG  ,  4
산업/NNG;생산/NNG;지표/NNG;호전/NNG  ,  2
fed/NNG;인플레이션/NNG;잘/MAG;통제/NNG  ,  1
가격/NNG;상승/NNG;최대/NNG  ,  15
낙관론/NNG;강하/VA  ,  3
역술/NNG  ,  5
犬馬之勞/NNG  ,  1
판타지/NNG  ,  15
집사람/NNG  ,  6
먹인다/VV  ,  3

발행/NNG;압력/NNG;부담/NNG  ,  5
알파인/NNG  ,  5
머물렀었/VV  ,  8
소비자/NNG;기대/NNG;지수/NNG;개선/NNG  ,  6
소비/NNG;심리/NNG;호전/NNG  ,  10
지수/NNG;경기/NNG;회복/NNG  ,  9
개선/NNG;금리/NNG;상승/NNG  ,  13
부승/NNG  ,  3
의연히/MAG  ,  4
경제/NNG;여건/NNG;긍정적/VAX  ,  4
역내/NNG;금리/NNG;인상/NNG  ,  10
콜/NNG;금리/NNG;목표/NNG;경기/NNG;회복/NNG  ,  8
수출/NNG;호조/NNG;소비/NNG;회복/NNG  ,  13
투자/NNG;신장/NNG  ,  11
경상/NNG;수지/NNG;적자/NNG;악화/NNG  ,  5
여력/NNG;높/VA;않/VX  ,  10
건전성/NNG;견조/NNG  ,  7
금리/NNG;정책/NNG;경기/NNG;회복/NNG  ,  2
근원/NNG;인플레이션/NNG;물가/NNG;안정/NNG  ,  9
금융안정/NNG;노력/NNG;강화/NNG  ,  10
순계/NNG  ,  1
하락/NNG;영향/NNG;제한/NNG  ,  3
通貨/NNG  ,  3
信用/NNG  ,  4
政策/NNG  ,  4
運營/NNG  ,  2
與件/NNG  ,  2
實物/NNG  ,  2
外換/NNG  ,  2
市場/NNG  ,  7
채권시장/NNG;최악/NNG  ,  6
개선/NNG;부담/NNG  ,  11
이류/NNG  ,  3
많/VA;금리/NNG;하락/NNG  ,  12
경기/NNG;회복/NNG;해치/VV  ,  7
종년/NNG  ,  1
채권/NNG;금리/NNG;하락/NNG;되돌/VV  ,  5
금리/NNG;국고채/NNG;오르/VV  ,  7
얄궂/VA  ,  13
하필/NNG  ,  8
수처/NNG  ,  11
우스꽝/NNG  ,  9
협기/NNG  ,  1
종결/NNG;가능성/NNG;높/VA  ,  4
오재/NNG  ,  8
절상/NNG;압력/NNG;크/VV  ,  11
불러들여/VV  , 

못했으며/VA  ,  4
국고채/NNG;내리/VV;떨어/VV  ,  8
선행/NNG;지표/NNG;지수선물/NNG;상승/NNG  ,  2
생산자/NNG;물가/NNG;안정/NNG  ,  11
생산자/NNG;물가/NNG;증가/NNG  ,  14
물가/NNG;하락/NNG;상승/NNG  ,  3
국제/NNG;유가/NNG;악재/NNG  ,  15
발자욱/NNG  ,  2
인전/NNG  ,  9
일시적/VAX;금리/NNG;하락/NNG  ,  12
은행/NNG;건전성/NNG;확보/NNG  ,  12
제로베이스/NNG  ,  11
보냅니다/VV  ,  4
아직/MAG;경기/NNG;회복/NNG;불확실/NNG  ,  1
가격/NNG;급락/NNG;금리/NNG;급등/NNG  ,  10
차가웠/VA  ,  11
피해/NNG;많/VA  ,  5
글로벌소싱/NNG  ,  4
증류/NNG  ,  14
소매/NNG;판매가격/NNG;높/VA  ,  6
ecb/NNG;금리/NNG;인상/NNG;가능성/NNG;약화/NNG  ,  8
약화/NNG;환율/NNG;상승/NNG  ,  5
당분간/MAG;회복/NNG;어렵/VA  ,  2
인상/NNG;신호/NNG;약하/VA  ,  2
적자/NNG;예상/NNG;작/VA  ,  5
수평선/NNG  ,  12
꿈틀거렸/VV  ,  6
금리/NNG;인상/NNG;국채/NNG;수익률/NNG;상승/NNG  ,  8
국채/NNG;수익률/NNG;최대/NNG  ,  11
소비자/NNG;지출/NNG;둔화/NNG  ,  12
달러자산/NNG;줄/VV  ,  14
촐라/NNG  ,  3
종료/NNG;양적완화/NNG  ,  7
급락/NNG;금리/NNG;급등/NNG  ,  5
유가/NNG;원자재/NNG;가격/NNG;불안/NNG  ,  15
물가/NNG;예상밖/NNG;상승/NNG  ,  5
천금/NNG  ,  6
한단/XSV  ,  10
경제/NNG;인상/NNG  ,  12
완만/NNG;속도/NNG;증가/NNG  ,  15
경기/NNG;회복/NNG;확장/NNG  ,  8
물가/NNG;경계

방조제/NNG  ,  7
끝막/NNG  ,  1
교토협약/NNG  ,  2
발굽/NNG  ,  1
fed/NNG;경계/NNG;약세/NNG  ,  5
상아탑/NNG  ,  10
상이점/NNG  ,  3
小考/NNG  ,  3
성장/NNG;기대/NNG;높/VV  ,  13
자금/NNG;조달/NNG;금리/NNG;하락/NNG  ,  7
원재료/NNG;가격/NNG;급등/NNG  ,  12
이익/NNG;변동성/NNG;높/VA  ,  5
장섬유/NNG  ,  6
금리/NNG;오르/VV;콜/NNG;금리/NNG;인상/NNG  ,  15
유가/NNG;하락/NNG;막/VV  ,  15
주택담보대출/NNG;조건/NNG;강화/NNG  ,  8
핵심/NNG;pce/NNG;물가/NNG;상승/NNG  ,  11
핵심/NNG;인플레이션/NNG;높/VA  ,  10
가처분/NNG;소득/NNG;높/VA  ,  1
ecb/NNG;금리/NNG;오르/VV;가능성/NNG;높/VA  ,  5
무반응/NNG  ,  12
부채/NNG;이자/NNG;부담/NNG;줄/VV  ,  5
원자재/NNG;가격/NNG;부담/NNG  ,  15
지표/NNG;예상/NNG;악화/NNG  ,  6
세계/NNG;최대/NNG;떨어/VV  ,  13
하락/NNG;수익률/NNG;상승/NNG  ,  5
전망/NNG;통제/NNG  ,  7
잠재/NNG;인플레이션/NNG;위험/NNG  ,  5
인플레이션/NNG;위험/NNG;차단/NNG  ,  15
權座/NNG  ,  1
야야/NNG  ,  3
높/VA;가격/NNG;인플레이션/NNG;압력/NNG  ,  6
재벌세/NNG  ,  14
황서/NNG  ,  11
가로챘/VV  ,  14
복역/NNG  ,  14
호주달러/NNG;절상/NNG  ,  14
fed/NNG;예상/NNG;강하/VA  ,  4
fed/NNG;금리/NNG;인상/NNG;하락/NNG  ,  6
기대/NNG;유가/NNG;하락/NNG  ,  15
금리/NNG;예상/NNG;오르/VV  ,  7
놀란다는/VV  ,  1
금리/NNG;인

국제피셔효과/NNG  ,  1
환차손익/NNG  ,  8
시달려서/VV  ,  2
그럴까/VA  ,  5
ecb/NNG;금리/NNG;인상/NNG;매파/NNG  ,  7
미/NNG;국채/NNG;수요/NNG;증가/NNG  ,  10
인상/NNG;불구/NNG;금리/NNG;하락/NNG  ,  1
인상/NNG;과도/NNG  ,  8
그릴지/VV  ,  8
콜/NNG;금리/NNG;인상/NNG;금리/NNG;상승/NNG  ,  4
단기/NNG;금리/NNG;소폭/MAG;상승/NNG  ,  9
금리/NNG;cd/NNG;금리/NNG;오르/VV  ,  11
금리/NNG;인상/NNG;금융시장/NNG;불확실성/NNG  ,  1
해이/XSV  ,  7
덕수/NNG  ,  13
화갑/NNG  ,  1
특감/NNG  ,  9
韓國/NNG  ,  5
순혈/NNG  ,  1
폐쇄성/NNG  ,  10
지자제/NNG  ,  2
인상/NNG;압력/NNG;낮/VA  ,  6
감미/NNG  ,  3
투자심리/NNG;안정/NNG;긍정적/VAX  ,  11
콜/NNG;금리/NNG;인상/NNG;하락/NNG  ,  6
경기/NNG;강하/VA;회복/NNG  ,  14
지켜져/VV  ,  12
드높이/VV  ,  8
위협/NNG;경고/NNG  ,  14
휴설/NNG  ,  3
태권도/NNG  ,  8
민속/NNG  ,  14
경원선/NNG  ,  10
동승자/NNG  ,  4
가까와짐/VA  ,  1
소비/NNG;설비/NNG;투자/NNG;내수/NNG;회복/NNG  ,  12
채권시장/NNG;정책/NNG;불확실성/NNG  ,  1
생산/NNG;활동/NNG;개선/NNG  ,  3
인상/NNG;해소/NNG  ,  1
급속/NNG;경제/NNG;성장/NNG  ,  13
ff/NNG;금리/NNG;넘/VV  ,  8
들썩거릴/VV  ,  3
금리/NNG;인상/NNG;통화/NNG;강세/NNG  ,  8
금리/NNG;인상/NNG;기대/NNG;약세/NNG  ,  5
이론/NNG;금리/NNG;인상/NNG  ,  6
한미/NNG;금

...

입마개/NNG  ,  5
석제/NNG  ,  1
문화대혁명/NNG  ,  1
국제기능올림픽대회/NNG  ,  1
넉넉잡/VV  ,  1
경기/NNG;회복/NNG;기대/NNG;금리/NNG;인하/NNG  ,  1
동액/NNG  ,  1
대론/NNG  ,  2
신검/NNG  ,  4
야해/VA  ,  1
헛똑똑이/NNG  ,  1
추명/NNG  ,  3
가격/NNG;급락/NNG;위험/NNG  ,  1
확장/NNG;가능성/NNG;높/VA  ,  2
병리/NNG  ,  1
침체/NNG;수요/NNG;둔화/NNG  ,  1
금리/NNG;비교/NNG;하락/NNG  ,  1
당분간/MAG;수요측면/NNG;물가/NNG;상승/NNG;압력/NNG  ,  3
공형/NNG  ,  2
진청/NNG  ,  2
유악/NNG  ,  1
회사채/NNG;금리/NNG;비교/NNG;내리/VV  ,  7
자산부채관리위원회/NNG  ,  4
시트커버/NNG  ,  4
경기/NNG;회복/NNG;gdp/NNG;갭/NNG;플러스/NNG  ,  1
국채/NNG;투자수익률/NNG;높/VA  ,  1
신용/NNG;대출/NNG;상승/NNG  ,  5
인상/NNG;미루/VV;어렵/VA  ,  2
감정풀이/NNG  ,  1
유통통화/NNG  ,  3
글로벌/NNG;경기/NNG;회복/NNG;확대/NNG  ,  1
대중/NNG;교역/NNG;여건/NNG;개선/NNG  ,  3
경기/NNG;물가/NNG;금융안정/NNG  ,  5
올빼미파/NNG  ,  4
낙태죄/NNG  ,  9
적이/VV  ,  1
시루/NNG  ,  1
씨네/NNG  ,  11
걸어갔/VV  ,  1
하향/NNG;신용등급/NNG;전망/NNG;부정적/VAX  ,  1
공용시설/NNG  ,  3
심박동/NNG  ,  1
여요/NNG  ,  1
어우러짐/VV  ,  1
아나키스트/NNG  ,  1
어설피/MAG  ,  1
코나/NNG  ,  5
양매/NNG  ,  2
강의료/NNG  ,  1
요공/NNG  ,  1
재무/NNG;부담/NNG;개선/NNG  ,  

소득/NNG;가계/NNG;부채/NNG;증가/NNG  ,  2
휴면국민주/NNG  ,  1
하락/NNG;호전/NNG  ,  1
특별부가세/NNG  ,  3
회복/NNG;정치/NNG;불확실성/NNG  ,  1
시흥교/NNG  ,  6
달아올랐으나/VV  ,  1
혁신당/NNG  ,  1
로렌초/NNG  ,  1
가리비/NNG  ,  2
팔립니다/VV  ,  1
저점/NNG;늘/VV  ,  1
업황/NNG;오르/VV  ,  1
군집효과/NNG  ,  1
양떼효과/NNG  ,  1
휘저으며/VV  ,  1
가입식/NNG  ,  1
열라/MAG  ,  1
구취/NNG  ,  1
잼버리/NNG  ,  4
유치새/NNG  ,  1
代作/NNG  ,  2
대물변제/NNG  ,  1
호안/NNG  ,  1
무한궤도/NNG  ,  1
신용등급/NNG;늘/VV  ,  1
설계대/NNG  ,  1
정치/NNG;리더십/NNG;약화/NNG  ,  1
fed/NNG;금리/NNG;인상/NNG;확률/NNG;하락/NNG  ,  1
둔화/NNG;금리/NNG;낮/VV  ,  1
가른다고/VV  ,  1
아리안로켓/NNG  ,  1
유르트/NNG  ,  1
성공/NNG;증가/NNG  ,  1
인터넷가전/NNG  ,  1
前代/NNG  ,  1
금리/NNG;연고점/NNG;상승/NNG  ,  1
인상/NNG;양적완화/NNG;축소/NNG  ,  1
팽창/NNG;긴축/NNG  ,  1
전염병채권/NNG  ,  1
잠마리/NNG  ,  1
스튜어드/NNG  ,  3
화생방/NNG  ,  1
과선교/NNG  ,  1
자본비율/NNG;상향/NNG  ,  2
형명/NNG  ,  3
인상/NNG;불확실성/NNG;상승/NNG  ,  1
생산/NNG;증가/NNG;높/VA  ,  1
인상/NNG;fed/NNG;자산/NNG;축소/NNG  ,  1
팔린다고/VV  ,  1
에덴동산/NNG  ,  1
성장/NNG;감안/NNG;금리/NNG;인상/NNG  ,  1
태소/NNG  ,  1
수출금액/NNG;늘/VV  ,  1
산골

가졌었으나/VV  ,  1
축판/NNG  ,  1
갈는지/VV  ,  1
레닌/NNG  ,  2
眞意/NNG  ,  1
타격점/NNG  ,  2
고참병/NNG  ,  1
아아/NNG  ,  14
캐리/NNG;투자/NNG;매력/NNG;높/VA  ,  3
신용스프레드/NNG;연저점/NNG  ,  2
내채/NNG  ,  3
바젤i/NNG  ,  1
음순/NNG  ,  1
조건부/NNG;자본증권/NNG;발행/NNG;증가/NNG  ,  1
자본/NNG;최저/NNG  ,  1
역저/NNG  ,  1
억한/NNG  ,  2
민간/NNG;성장/NNG;모멘텀/NNG  ,  1
연선/NNG  ,  2
하락/NNG;경기/NNG;선행/NNG;지수/NNG;상승/NNG  ,  1
자이나교/NNG  ,  2
인간사/NNG  ,  1
폭폭폭폭/MAG  ,  1
큰일날/VV  ,  1
금리/NNG;급락/NNG;금리/NNG;하락/NNG  ,  1
자본/NNG;개선/NNG  ,  1
원화/NNG;약세/NNG;crs/NNG;금리/NNG;하락/NNG  ,  1
채권/NNG;금리/NNG;상단/NNG;제한/NNG  ,  7
국채선물/NNG;매수/NNG;약화/NNG  ,  1
과과/NNG  ,  6
fed/NNG;금리/NNG;자산/NNG;축소/NNG  ,  1
개선/NNG;경기/NNG;모멘텀/NNG  ,  1
완화/NNG;강도/NNG;줄/VV  ,  2
완화/NNG;제거/NNG  ,  1
도순/NNG  ,  5
금리/NNG;인상/NNG;소수의견/NNG;금리/NNG;인상/NNG  ,  1
국고채/NNG;상승/NNG;국고채/NNG;하락/NNG  ,  1
만기구간/NNG;금리/NNG;상승/NNG  ,  1
글로벌/NNG;완화정책/NNG;강화/NNG  ,  5
성장/NNG;인플레이션/NNG;압력/NNG;서서히/MAG;충족/NNG  ,  6
속일지라도/VV  ,  1
傲慢/NNG  ,  2
저지른다/VV  ,  1
크레딧/NNG;투자/NNG;수요/NNG;견조/NNG  ,  3
하락/NNG;상승/NNG;하락/NN

자금/NNG;우려/NNG;확대/NNG  ,  1
자금/NNG;우려/NNG;높/VA  ,  2
리벳/NNG  ,  1
선박국/NNG  ,  1
전기수/NNG  ,  4
수정목/NNG  ,  2
개시호/NNG  ,  2
수요곡선/NNG  ,  2
회복/NNG;신용스프레드/NNG;축소/NNG  ,  2
투기등급/NNG;투자등급/NNG;상향/NNG  ,  1
회사채/NNG;스프레드/NNG;강세/NNG  ,  2
기대/NNG;정치/NNG;불확실성/NNG  ,  1
외환보유액/NNG;회복/NNG  ,  2
투자등급/NNG;확대/NNG  ,  3
선진국/NNG;채권/NNG;금리/NNG;하락/NNG  ,  1
금리/NNG;안정/NNG;금리/NNG;인상/NNG  ,  1
불확실성/NNG;지지/NNG  ,  1
인상/NNG;우려/NNG;채권/NNG;금리/NNG;상승/NNG  ,  1
양원제/NNG  ,  2
임명권/NNG  ,  1
인하/NNG;명분/NNG;강화/NNG  ,  1
축차/NNG  ,  1
인상/NNG;의지/NNG;강하/VA  ,  1
여전채/NNG;회사채/NNG;스프레드/NNG;확대/NNG  ,  4
재무/NNG;융통성/NNG;저하/NNG  ,  4
완화/NNG;채권/NNG;금리/NNG;하락/NNG  ,  1
악화/NNG;급등/NNG  ,  1
개선/NNG;미/NNG;금리/NNG;인상/NNG  ,  1
예상/NNG;장기/NNG;금리/NNG;하락/NNG  ,  1
하향/NNG;경기/NNG;불확실성/NNG  ,  1
기대/NNG;하향/NNG;안정/NNG  ,  3
바루/MAG  ,  3
국고채/NNG;스프레드/NNG;금리/NNG;인하/NNG  ,  1
엘엔지/NNG  ,  10
충분/NNG;투자/NNG;수요/NNG;확보/NNG  ,  4
투자/NNG;재무/NNG;부담/NNG;확대/NNG  ,  2
장기물/NNG;신용스프레드/NNG;확대/NNG  ,  1
자립성/NNG  ,  4
장단기스프레드/NNG;확대/NNG;압력/NNG;우세/NNG  ,  1
부양/NNG;쉽/VA

채권/NNG;금리/NNG;단기물/NNG;하락/NNG  ,  1
인플레이션/NNG;소폭/MAG;하락/NNG  ,  1
지담/NNG  ,  1
활경/NNG  ,  1
자법/NNG  ,  1
민세/NNG  ,  1
거영/NNG  ,  1
금리/NNG;전망/NNG;약세/NNG  ,  1
아이엔에스/NNG  ,  1
채농/NNG  ,  1
지표/NNG;열위/NNG  ,  1
신용스프레드/NNG;회사채/NNG;축소/NNG  ,  1
하향/NNG;경제/NNG;회복/NNG  ,  1
높/VA;등급/NNG;하락/NNG  ,  2
산업활동/NNG;상승/NNG  ,  1
어회/NNG  ,  1
복국/NNG  ,  1
상회/NNG;호조/NNG  ,  1
어렴/NNG  ,  1
국고채/NNG;금리/NNG;하락/NNG;스프레드/NNG;확대/NNG  ,  1
크레딧/NNG;국고채/NNG;금리/NNG;하락/NNG  ,  1
크레딧/NNG;가격/NNG;부담/NNG  ,  1
하향/NNG;불확실성/NNG  ,  1
단기물/NNG;일시적/VAX  ,  1
생산자제품재고지수/NNG  ,  1
금리/NNG;추이/NNG;금리/NNG;상승/NNG  ,  1
커버넌트/NNG  ,  2
사채발행요건/NNG  ,  1
국고채/NNG;발행/NNG;유보/NNG  ,  1
총교/NNG  ,  1
인상/NNG;국채/NNG;금리/NNG;상승/NNG  ,  1
감극/NNG  ,  1
선진국/NNG;금리/NNG;하향/NNG  ,  1


In [125]:
b.drop(b.index[index_list], inplace = True)

In [127]:
b.to_csv('data/news_bond_mpb_intensity_cut.csv', index = False)

In [45]:
b['sentiment'] = pd.Series()

In [47]:
b.to_csv('data/news_bond_mpb_intensity.csv', index = False)

In [48]:
b = pd.read_csv('data/news_bond_mpb_intensity.csv')

In [50]:
a_index = b.index[b['polarity'] >= 1].tolist()

for index in a_index:

    b['sentiment'].set_value(index, '1')

a_index2 = b.index[b['polarity'] < 1].tolist()

for index in a_index2:

    b['sentiment'].set_value(index, '-1')

/usr/lib/python3/dist-packages/ipykernel_launcher.py:5: FutureWarning: set_value is deprecated and will be removed in a future release. Please use .at[] or .iat[] accessors instead
  """
/usr/lib/python3/dist-packages/ipykernel_launcher.py:11: FutureWarning: set_value is deprecated and will be removed in a future release. Please use .at[] or .iat[] accessors instead
  # This is added back by InteractiveShellApp.init_path()


In [51]:
b.to_csv('data/news_bond_mpb_sentiment.csv', index = False)

In [52]:
b

word  Hawkish  Dovish      Haw_prob  \
0                            주택시장/NNG;과열/NNG       33      58  1.732230e-06   
1                              경기/NNG;침체/NNG     1085    1859  5.612941e-05   
2                                      임할/VV       18      48  9.566044e-07   
3                                     종합/NNG    16923   26097  8.750862e-04   
4                                     새해/NNG     2100    1067  1.086134e-04   
5                                     전조/NNG      139     103  7.213314e-06   
6                                     마다/NNG      167     134  8.661148e-06   
7                                   일어났으며/VV        6       4  3.361042e-07   
8                                     과열/NNG     3025    2346  1.564436e-04   
9                                     인하/NNG    48173   82082  2.490972e-03   
10                                    휴가/NNG      559     446  2.893082e-05   
11                                    인상/NNG   119925   95773  6.201149e-03   
12                          기대/NNG;작/VA;않/VX       41      28  2.145896e-06   
13                                    납회/NNG        8       3  4.395209e-07   
14                                    구랍/NNG       21       8  1.111729e-06   
15                                     맛봤/VV       24      16  1.266854e-06   
16                                    포진/NNG      238     186  1.233244e-05   
17                                  전인미답/NNG       24      15  1.266854e-06   
18                                    발회/NNG        1       0  7.756252e-08   
19                                    그해/NNG      121     177  6.282564e-06   
20                                  추정실적/NNG       11       3  5.946460e-07   
21                                    반월/NNG      311     238  1.610715e-05   
22                                   하반부/NNG        1       0  7.756252e-08   
23                                   주도력/NNG       43      26  2.249313e-06   
24              하락/NNG;원자재/NNG;가격/NNG;상승/NNG        7      11  3.878126e-07   
25                      건설/NNG;투자/NNG;부진/NNG       82      28  4.265939e-06   
26                      무역/NNG;재정/NNG;적자/NNG        9       4  4.912293e-07   
27                       심리/NNG;서서히/MAG;살/VV       10       6  5.429376e-07   
28                             경기/NNG;부진/NNG      425     633  2.200190e-05   
29                             경제/NNG;최악/NNG       34      63  1.783938e-06   
...                                      ...      ...     ...           ...   
96982                                 활경/NNG        1       0  7.756252e-08   
96983                                 자법/NNG        1       0  7.756252e-08   
96984                                 민세/NNG        1       0  7.756252e-08   
96985                                 거영/NNG        1       0  7.756252e-08   
96986                   금리/NNG;전망/NNG;약세/NNG        1       0  7.756252e-08   
96987                              아이엔에스/NNG        0       1  2.585417e-08   
96988                                 채농/NNG        0       1  2.585417e-08   
96989                          지표/NNG;열위/NNG        0       1  2.585417e-08   
96990              신용스프레드/NNG;회사채/NNG;축소/NNG        0       1  2.585417e-08   
96991                   하향/NNG;경제/NNG;회복/NNG        0       1  2.585417e-08   
96992                     높/VA;등급/NNG;하락/NNG        0       2  2.585417e-08   
96993                        산업활동/NNG;상승/NNG        0       1  2.585417e-08   
96994                                 어회/NNG        1       0  7.756252e-08   
96995                                 복국/NNG        1       0  7.756252e-08   
96996                          상회/NNG;호조/NNG        1       0  7.756252e-08   
96997                                 어렴/NNG        0       1  2.585417e-08   
96998  국고채/NNG;금리/NNG;하락/NNG;스프레드/NNG;확대/NNG        0       1  2.585417e-08   
96999          크레딧/NNG;국고채/NNG;금리/NNG;하락/NNG        0       1  2.585417e-08   
97000                  크레딧/NNG;가격/NNG;부담/NNG        0       1  2.585417e-08   
97001      

In [39]:
b.to_csv('data/news_bond_mpb_sentiment_cut.csv', index = False)

In [136]:
a = pd.read_csv('data/news_bond_mpb_sentiment.csv')

In [140]:
b = pd.read_csv('data/news_bond_mpb_sentiment_cut.csv')